In [41]:
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np
import random
import osmnx as ox
import pickle

random.seed(112)

In [42]:
run_experiments = False

city = 'Manhattan'
run_length = 1800
filepath = f"graphs/{city}.graph.graphml"
graph = ox.load_graphml(filepath=filepath)

In [43]:
# import fug data
with open(f'data/fugitive_start_{city}.pkl', 'rb') as f:
    fugitive_start = pickle.load(f)
with open(f'data/escape_nodes_{city}.pkl', 'rb') as f:
    escape_nodes = pickle.load(f)
with open(f'data/results_routes_randomwalk_{city}.pkl', 'rb') as f:
    results_routes = pickle.load(f)

# import police data
with open(f'data/optimization/start_police_{city}.pkl', 'rb') as f:
    police_start = pickle.load(f)
with open(f'data/optimization/delays_police_{city}.pkl', 'rb') as f:
    delays = pickle.load(f)

In [44]:
def escape_route(graph, fugitive_start, escape_nodes, T):
    walk = {}
    node = fugitive_start
    walk[0] = node
    previous_node = node

    while max(walk.keys()) < T:
        if node in escape_nodes:
            return walk
        
        list_neighbor = list(graph.neighbors(node))
        #
        # if max(walk.keys()) == 0:
        #     nextnode = random.choice(list_neighbor)

        # exclude previous node for 'normal' walk
        # don't do this for dead ends
        if len(list_neighbor) > 1:
            if previous_node in list_neighbor:
                list_neighbor.remove(previous_node)

        if len(list_neighbor) != 0:
            nextnode = random.choice(list_neighbor)

            time_at_node = max(walk.keys()) + float(graph[node][nextnode][0.0]['travel_time'])
            walk[time_at_node] = nextnode

        else:  # no feasible neighbors
            if node == previous_node:
                return walk

            else:
                nextnode = previous_node

                time_at_node = max(walk.keys()) + float(graph[previous_node][node][0.0]['travel_time'])
                walk[time_at_node] = nextnode

        # save previous node
        previous_node = node

        node = nextnode

    return walk

In [45]:
# results_routes = []
# for i in range(1000):
#     route = escape_route(graph, fugitive_start, escape_nodes, run_length)
#     results_routes.append(route)

# with open(f'data/results_routes_randomwalk_{city}.pkl', 'wb') as f:
#     pickle.dump(results_routes, f)

In [46]:
results_routes

[{0: 4597668023,
  7.3: 4597668035,
  15.600000000000001: 42428493,
  40.6: 42440710,
  68.3: 42430253,
  92.8: 42439823,
  100.7: 42429375,
  107.9: 42439073,
  132.3: 42430249,
  160.0: 42439070,
  175.6: 42446521,
  182.9: 42436935,
  199.0: 42429373,
  206.3: 42439070,
  213.5: 42449067,
  241.2: 42430247,
  248.5: 42430249,
  255.7: 42429374,
  280.2: 42429375,
  299.2: 42429378,
  305.9: 42432211,
  311.0: 42432208,
  320.6: 42439073,
  327.8: 42430828,
  334.1: 42432205,
  339.5: 42432208,
  349.1: 42439073,
  373.5: 42430249,
  380.7: 42429374,
  388.59999999999997: 42430253,
  416.29999999999995: 42440710,
  441.29999999999995: 42428493,
  448.59999999999997: 42440721,
  457.59999999999997: 42431452,
  458.59999999999997: 4597668035,
  466.9: 42428493,
  491.9: 42440710,
  519.6: 42430253,
  527.4: 42430255,
  552.0: 42439826,
  576.3: 42435598,
  583.4: 42435599,
  607.9: 42439830,
  615.1: 42439826,
  622.9: 42439823,
  647.1999999999999: 42435596,
  655.1999999999999: 42435

In [47]:
results_routes_list = [list(route.values()) for route in results_routes]

In [48]:
# from optimize.plot_results_optimization import draw_nodes, draw_edges
# 
# node_size, node_color = draw_nodes(graph, fugitive_start, escape_nodes, [], [])
# edge_colormap, edge_weightmap = draw_edges(graph)
# 
# fig, ax = ox.plot_graph_routes(graph, results_routes_list,
#                                route_linewidths=1, route_alphas = [0.1]*len(results_routes),
#                                edge_linewidth=edge_weightmap, edge_color=edge_colormap,
#                                node_color=node_color, node_size=node_size,
#                                bgcolor="white",
#                                orig_dest_size=30,
#                                show=False,
#                                # orig_dest_node_color=['tab:orange', 'tab:red']*len(results_routes),
#                                )
# fig.savefig(f'graphs/routes_randomwalk_{city}.png', bbox_inches='tight', dpi=300)

# Optimize pol routes

In [49]:
def FIP_model(route_fugitive_labeled=None, run_length=None, tau_uv=None, labels_full_sorted=None, labels_sorted=None,
              labels_sorted_inv=None,
              **kwargs):
    pi_uv = {}
    z_r = {}
    pi_nodes = []

    for u, value in enumerate(list(kwargs.values())):
        associated_node = labels_sorted_inv[int(u)][int(np.floor(value))]
        pi_nodes.append(labels_full_sorted[associated_node])

    for i_r, _ in enumerate(route_fugitive_labeled):
        z_r[i_r] = 0

    for i_r, r in enumerate(route_fugitive_labeled):  # for each route
        if any([node in pi_nodes for node in r.values()]):
            for u, pi in enumerate(pi_nodes):  # for each police unit
                for time_at_node_fugitive, node_fugitive in r.items():  # for each node in the fugitive route
                    if node_fugitive == pi:  # if the fugitive node is the same as the target node of the police unit
                        if time_at_node_fugitive > tau_uv[u, node_fugitive]:  # and the police unit can reach that node
                            z_r[i_r] = 1  # intercepted

    return [float(sum(z_r.values()))]

In [50]:
def get_intercepted_routes(route_fugitive_labeled, tau_uv, labels_full_sorted, labels_sorted_inv, results_positions):
    z_r = {}
    pi_nodes = []

    for u, value in enumerate(results_positions):
        associated_node = labels_sorted_inv[int(u)][int(np.floor(value))]
        pi_nodes.append(labels_full_sorted[associated_node])

    for i_r, _ in enumerate(route_fugitive_labeled):
        z_r[i_r] = 0

    for i_r, r in enumerate(route_fugitive_labeled):  # for each route
        if any([node in pi_nodes for node in r.values()]):
            for u, pi in enumerate(pi_nodes):  # for each police unit
                for time_at_node_fugitive, node_fugitive in r.items():  # for each node in the fugitive route
                    if node_fugitive == pi:  # if the fugitive node is the same as the target node of the police unit
                        if time_at_node_fugitive > tau_uv[u, node_fugitive]:  # and the police unit can reach that node
                            z_r[i_r] = 1  # intercepted

    # print(sum(z_r.values())/500)

    # for r in range(len(route_fugitive_labeled)):
    #     z_r[r] = sum(sum(sum(pi_uv[u, v] * phi_rt[r, t, v] * tau_uv[u, t, v] for v in labels_full_sorted.values()) for u in range(U)) for t in range(run_length))

    return z_r

In [51]:
from ema_workbench import MultiprocessingEvaluator, SequentialEvaluator
from ema_workbench import RealParameter, ScalarOutcome, Constant, Model
from ema_workbench.em_framework.optimization import ArchiveLogger, SingleObjectiveBorgWithArchive

from optimize.sort_and_filter import sort_and_filter_pol_fug_city as sort_and_filter_nodes
from optimize.unit_ranges import unit_ranges


def optimize(graph, fugitive_start, results_routes, police_stations, delays, run_length):

    # sort indices on distance to start_fugitive
    labels_perunit_sorted, labels_perunit_inv_sorted, labels_full_sorted = sort_and_filter_nodes(graph,
                                                                                                 fugitive_start,
                                                                                                 results_routes,
                                                                                                 police_stations,
                                                                                                 run_length)
    print('labels done')

    route_fugitive_labeled = []
    for r in results_routes:
        r_labeled = {x: labels_full_sorted[y] for x, y in r.items()}
        route_fugitive_labeled.append(r_labeled)

    tau_uv = unit_ranges(start_units=police_stations, delays=delays, U=len(police_stations), G=graph, L=run_length,
                         labels_full_sorted=labels_full_sorted)
    print('tau_uv done')
    
    upper_bounds = []
    for u in range(len(police_stations)):
        if len(labels_perunit_sorted[u]) <= 1:
            upper_bounds.append(0.999)
        else:
            upper_bounds.append(len(labels_perunit_sorted[u]) - 0.001)  # different for each unit

    model = Model("FIPEMA", function=FIP_model)

    model.levers = [RealParameter(f"pi_{u}", 0, upper_bounds[u]) for u in range(len(police_stations))]

    model.constants = model.constants = [
        Constant("route_fugitive_labeled", route_fugitive_labeled),
        Constant("run_length", run_length),
        Constant("tau_uv", tau_uv),
        Constant("labels_full_sorted", labels_full_sorted),
        Constant("labels_sorted", labels_perunit_sorted),
        Constant("labels_sorted_inv", labels_perunit_inv_sorted)
    ]

    model.outcomes = [
        ScalarOutcome("pct_intercepted", kind=ScalarOutcome.MAXIMIZE)
    ]

    print('start optimize')
    highest_perf = 0
    with SequentialEvaluator(model) as evaluator:
        for _ in range(5):
            convergence_metrics = [
                ArchiveLogger(
                    f"./results/optimization/",
                    [l.name for l in model.levers],
                    [o.name for o in model.outcomes if o.kind != o.INFO],
                    base_filename=f"archives_random_walk_{city}.tar.gz"
                ),
            ]

            result = evaluator.optimize(
                algorithm=SingleObjectiveBorgWithArchive,
                nfe=20000,
                searchover="levers",
                convergence=convergence_metrics,
                convergence_freq=100
            )

            result = result.iloc[0]
            if result['pct_intercepted'] > highest_perf:
                print('found better')
                results = result

    results_positions = []
    results_positions_labeled = []
    for u, start in enumerate(police_stations):
        results_positions.append(results[f'pi_{u}'])
        results_positions_labeled.append(labels_perunit_inv_sorted[u][int(np.floor(results[f'pi_{u}']))])
    # print(results_positions)

    routes_intercepted = get_intercepted_routes(route_fugitive_labeled,
                                            tau_uv,
                                            labels_full_sorted,
                                            labels_perunit_inv_sorted,
                                            results_positions
                                            )

    return results, routes_intercepted, results_positions_labeled

In [52]:
if run_experiments: 
    results, routes_intercepted, results_positions = optimize(graph, fugitive_start, results_routes, police_start, delays, run_length)
    
    with open(f'results/optimization/results_optimization_randomwalk_{city}.pkl', 'wb') as f:
        pickle.dump(results, f)
        
    with open(f'results/optimization/results_intercepted_routes_randomwalk_{city}.pkl', 'wb') as f:
        pickle.dump(routes_intercepted, f)
    
    with open(f'results/optimization/results_positions_randomwalk_{city}.pkl', 'wb') as f:
        pickle.dump(results_positions, f)
else:
    with open(f'results/optimization/results_optimization_randomwalk_{city}.pkl', 'rb') as f:
        results = pickle.load(f)
    with open(f'results/optimization/results_intercepted_routes_randomwalk_{city}.pkl', 'rb') as f:
        routes_intercepted = pickle.load(f)
    with open(f'results/optimization/results_positions_randomwalk_{city}.pkl', 'rb') as f:
        results_positions = pickle.load(f)

In [53]:
results_positions

[42434355, 42439823, 42446552, 5849918502, 42454423]

In [54]:
results

pi_0                10.213674
pi_1               156.151901
pi_2               264.607684
pi_3               366.632130
pi_4               523.511300
pct_intercepted    740.000000
Name: 0, dtype: float64

In [55]:
from optimize.plot_results_optimization import draw_nodes, draw_edges

police_routes = [ox.shortest_path(graph, police_start[u], results_positions[u]) for u, _ in enumerate(police_start)]

results_routes_list = [list(route.values()) for route in results_routes]
results_routes_list += police_routes

route_colors = ['tab:green' if val == 1 else 'tab:red' if val == 0 else ValueError for val in routes_intercepted.values()]
route_colors += ['tab:blue' for pol in police_routes]
route_alphas = [0.05 for fug in routes_intercepted]
route_alphas += [1 for pol in police_routes]

def draw_nodes(G, fugitive_start, escape_nodes, police_start, police_end):
    node_size = []
    node_color = []
    for node in G.nodes:
        if node in escape_nodes:
            node_size.append(30)
            node_color.append('tab:red')
        elif node in police_start:
            node_size.append(30)
            node_color.append('#51a9ff')
        elif node in police_end:
            node_size.append(30)
            node_color.append('tab:blue')
        elif node == fugitive_start:
            node_size.append(40)
            node_color.append('tab:orange')
        else:
            node_size.append(0)
            node_color.append('lightgray')
    return node_size, node_color

node_size, node_color = draw_nodes(graph, fugitive_start, escape_nodes, police_start, results_positions)
edge_colormap, edge_weightmap = draw_edges(graph)
# edge_weightmap = [0] * len(graph.edges())

In [56]:
# fig, ax = ox.plot_graph_routes(graph, results_routes_list,
#                                route_linewidths=1, route_alphas=route_alphas, route_colors=route_colors,
#                                edge_linewidth=edge_weightmap, edge_color=edge_colormap,
#                                node_color=node_color, node_size=node_size,
#                                bgcolor="white",
#                                orig_dest_size=30,
#                                show=False,
#                                # orig_dest_node_color=['tab:orange', 'tab:red']*len(results_routes),
#                                )
# 
# fig.savefig(f'results/optimization_onlyroutes_randomwalk_{city}.png', bbox_inches='tight', dpi=300)

# For results table in paper

In [57]:
from optimize.plot_results_optimization import draw_nodes, draw_edges

police_routes = [ox.shortest_path(graph, police_start[u], results_positions[u]) for u, _ in enumerate(police_start)]

results_routes_list = [list(route.values()) for route in results_routes]
# results_routes_list += police_routes

route_colors = ['tab:green' if val == 1 else 'tab:red' if val == 0 else ValueError for val in routes_intercepted.values()]
# route_colors += ['tab:blue' for pol in police_routes]
route_alphas = [0.05 for fug in routes_intercepted]
# route_alphas += [1 for pol in police_routes]
route_linewidths = [1 for fug in routes_intercepted]
# route_linewidths += [2 for pol in police_routes]

def draw_nodes(G, fugitive_start, escape_nodes, police_start, police_end):
    node_size = []
    node_color = []
    for node in G.nodes:
        if node in police_end:
            node_size.append(120)
            node_color.append('tab:blue')
        elif node in escape_nodes:
            node_size.append(20)
            node_color.append('tab:red')
        # elif node in police_start:
        #     node_size.append(60)
        #     node_color.append('tab:cyan')
        # elif node in police_start:
        #     node_size.append(60)
        #     node_color.append('#51a9ff')
        elif node == fugitive_start:
            node_size.append(40)
            node_color.append('tab:orange')
        else:
            node_size.append(0)
            node_color.append('lightgray')
    return node_size, node_color

node_size, node_color = draw_nodes(graph, fugitive_start, escape_nodes, police_start, results_positions)
edge_colormap, edge_weightmap = draw_edges(graph)
edge_weightmap = [0.3] * len(graph.edges())

In [58]:
fig, ax = ox.plot_graph_routes(graph, results_routes_list,
                               route_linewidths=route_linewidths, route_alphas=route_alphas, route_colors=route_colors,
                               edge_linewidth=edge_weightmap, edge_color=edge_colormap,
                               node_color=node_color, node_size=node_size, node_zorder=2,
                               bgcolor="white",
                               orig_dest_size=30,
                               show=False,
                               # orig_dest_node_color=['tab:orange', 'tab:red']*len(results_routes),
                               )

fig.savefig(f'results/optimization_positions_randomwalk_{city}.png', bbox_inches='tight', dpi=300)